In [14]:
import h5py
import time
import math
import numpy
from matplotlib import pyplot
import matplotlib.dates as mdates
from matplotlib.ticker import AutoMinorLocator, MultipleLocator
start_time = time.time()
new_colors=['#1f77b4', '#ff7f0e', '#2ca02c', '#d62728', '#9467bd', '#8c564b', '#e377c2', '#7f7f7f', '#bcbd22', '#17becf']

ticks = [0,3,6,9,12,15,18,21]
ax.set_yticks(ticks)

dic = { 0 : "19",3 : "22" ,6 : "1" ,9 : "4" ,12 : "7" ,15 : "10" ,18 : "13" ,21 : "16"} # JRO local time
locallabels = [ticks[i] if t not in dic.keys() else dic[t] for i,t in enumerate(ticks)]

# import matplotlib.pyplot as plt
'''
Reading HDF5 file
'''
datafolder=r'C:\Users\JmGomezs\Documents\Scintpi\data'
hdf5file  ='sc2_lvl2_20210314_0001_768758.0625W_119523.1016S.h5'

dic={}
gnsslist=['00','01','02','03','06']
# gnsslist=['00'] # only GPS
gnssdic={'00':'GPS','01':'SBS','02':'GAL','03':'BEI','06':'GLO'}
gnssname=['GPS','SBAS','GALILEO','BEIDOU','GLONAS']
in_fields =['S4L1','S4L2','ELEV','TIME','AZIT','NSA1','NSA2']
# out_fields=['S4L1','S4L2','ELEV','TIME','AZIT','NSA1','NSA2'] # 1 min resolution # add 1 min TEC
for GNSSid in gnssdic:
	for sat in range(0,38):
		for field in in_fields:
			dic["%s_%03d_%s"%(GNSSid,sat,field)] =[]

satlist=[131,133,136,138]
for sat in satlist:
    for field in in_fields:
#         print ("%s_%03d_%s"%('01',sat,field) )
        dic["%s_%03d_%s"%('01',sat,field)] =[]
            
maxsats = 0
h5filename = "%s/%s"%(datafolder,hdf5file)
print ("Reading %s file"%(h5filename))
h5file = h5py.File(h5filename,'r+')
for conste in h5file.keys():
	if conste == 'GPS':
		gnssid = '00'
	elif conste == 'SBS':
		gnssid = '01'    
	elif conste == 'GAL':
		gnssid = '02'
	elif conste == 'BEI':
		gnssid = '03'
	elif conste == 'GLO':
		gnssid = '06'
	groups = h5file.get(conste)
	for member in groups.items():
		maxsats = maxsats + 1
		svid = member[0].replace('SVID','')
		for each_param in groups.get(member[0]).keys():
# 			print ("%s_%s_%s"%(gnssid,svid,each_param))
			dic["%s_%03d_%s"%(gnssid,int(svid),each_param)] = groups.get(member[0]).get(each_param)[0]
h5file.close()
print ("maxsats:",maxsats)


#Initializing Figure :
pyplot.close('all')
pyplot.ioff()
maxcol = 5
maxrow = int(numpy.ceil(maxsats/maxcol))
fig, axs = pyplot.subplots(maxrow, maxcol, figsize=(12, 12), dpi=1200) #,constrained_layout = True

each_row = 0
each_col = 0
for GNSSid in gnsslist:
    if GNSSid != '01':
        for eachsat in range(1,38):
            notempty = len(dic["%s_%03d_TIME"%(GNSSid,eachsat)])

            if notempty != 0 :
                svid = "%2d"%eachsat
                if GNSSid == '00':
                    sc2_coid = 'GPS'+ svid
                elif GNSSid == '01':
                    sc2_coid = 'SBS'+ svid
                elif GNSSid == '02':
                    sc2_coid = 'GAL'+ svid
                elif GNSSid == '03':
                    sc2_coid = 'BEI'+ svid
                elif GNSSid == '06':
                    sc2_coid = 'GLO'+ svid

                #GETTING SR 1 MIN RESOLUTION DATA
                SC3_S4_1 = dic["%s_%03d_S4L1"%(GNSSid,eachsat)]
                SC3_TIME = dic["%s_%03d_TIME"%(GNSSid,eachsat)]
                SC3_ELEV = dic["%s_%03d_ELEV"%(GNSSid,eachsat)]/100.0
                SC3_AZIT = dic["%s_%03d_AZIT"%(GNSSid,eachsat)]/360.0
                axs[each_row, each_col].plot(SC3_TIME, SC3_S4_1,'-',color='#d62728',linewidth=0.8)
                axs[each_row, each_col].plot(SC3_TIME, SC3_ELEV,'-',color='#1f77b4',linewidth=0.8)
#                 axs[each_row, each_col].plot(SC3_TIME, SC3_AZIT,'-',color='#2ca02c',linewidth=0.8)
                axs[each_row, each_col].text(1,0.8,sc2_coid,fontsize=7,weight='bold')

                if each_col == 0:
                    axs[each_row, each_col].set_ylabel('S4 Sc2', fontsize = 7)
                    axs[each_row, each_col].set_xticks(numpy.arange(0, 24, step=3))  # Set label locations.
                    axs[each_row, each_col].set_yticks(numpy.arange(0, 1.1, step=0.25))  # Set label locations.
                    axs[each_row, each_col].grid(True,which='minor',linestyle='--',linewidth=0.1)
                    axs[each_row, each_col].grid(True,which='major',linestyle='--',linewidth=0.4)
                    axs[each_row, each_col].tick_params(axis='y',which='major', width=0.5, labelsize=5.5)#X and y labels font size
#                     pyplot.setp(axs[each_row, each_col].get_xmajorticklabels(), visible=False)
                    if each_row != (maxrow-1):
                        pyplot.setp(axs[each_row, each_col].get_xmajorticklabels(), visible=False)             

                if each_row == (maxrow-1):
                    axs[each_row, each_col].set_xlabel('Local Time', fontsize = 7)
                    axs[each_row, each_col].set_xticks(numpy.arange(0, 24, step=3))  # Set label locations.
                    axs[each_row, each_col].set_xticklabels(locallabels)
                    axs[each_row, each_col].set_yticks(numpy.arange(0, 1.1, step=0.25))  # Set label locations.
                    axs[each_row, each_col].grid(True,which='minor',linestyle='--',linewidth=0.1)
                    axs[each_row, each_col].grid(True,which='major',linestyle='--',linewidth=0.4)
                    axs[each_row, each_col].tick_params(axis='x',which='major', width=0.7, labelsize=7)#X and y labels font size
                    pyplot.setp(axs[each_row, each_col].get_xmajorticklabels(), visible=True)
#                     print (sc2_coid,each_col,each_row,'2')
                else:
                    axs[each_row, each_col].set_xticks(numpy.arange(0, 24, step=3))  # Set label locations.
                    axs[each_row, each_col].set_xticklabels(locallabels)
                    axs[each_row, each_col].set_yticks(numpy.arange(0, 1.1, step=0.25))  # Set label locations.
                    axs[each_row, each_col].grid(True,which='minor',linestyle='--',linewidth=0.1)
                    axs[each_row, each_col].grid(True,which='major',linestyle='--',linewidth=0.4)
                    pyplot.setp(axs[each_row, each_col].get_xmajorticklabels(), visible=False)
#                     print (sc2_coid,each_col,each_row,'3')

                axs[each_row, each_col].set_ylim(0, 1.1)
                axs[each_row, each_col].set_xlim(0, 24)
                each_col = each_col + 1
                if each_col == maxcol:
                    each_row=each_row+1
                    each_col = 0

    else:
        for eachsat in satlist:
            notempty = len(dic["%s_%03d_TIME"%(GNSSid,eachsat)] )
            if notempty != 0 :
                svid = "%03d"%eachsat
           
                if GNSSid == '00':
                    sc2_coid = 'GPS'+ svid
                elif GNSSid == '01':
                    sc2_coid = 'SBS'+ svid
                elif GNSSid == '02':
                    sc2_coid = 'GAL'+ svid
                elif GNSSid == '03':
                    sc2_coid = 'BEI'+ svid
                elif GNSSid == '06':
                    sc2_coid = 'GLO'+ svid

                #GETTING SR 1 MIN RESOLUTION DATA
                SC3_S4_1 = dic["%s_%03d_S4L1"%(GNSSid,eachsat)]
                SC3_TIME = dic["%s_%03d_TIME"%(GNSSid,eachsat)]
                SC3_ELEV = dic["%s_%03d_ELEV"%(GNSSid,eachsat)]/100.0
                SC3_AZIT = dic["%s_%03d_AZIT"%(GNSSid,eachsat)]/360.0
                axs[each_row, each_col].plot(SC3_TIME, SC3_S4_1,'-',color='#d62728',linewidth=0.8)
                axs[each_row, each_col].plot(SC3_TIME, SC3_ELEV,'-',color='#1f77b4',linewidth=0.8)
#                 axs[each_row, each_col].plot(SC3_TIME, SC3_AZIT,'-',color='#2ca02c',linewidth=0.8)
                axs[each_row, each_col].text(1,0.8,sc2_coid,fontsize=7,weight='bold')
                if each_col == 0:
                    axs[each_row, each_col].set_ylabel('S4 Sc2', fontsize = 7)
                    axs[each_row, each_col].set_xticks(numpy.arange(0, 24, step=3))  # Set label locations.
                    axs[each_row, each_col].set_yticks(numpy.arange(0, 1.1, step=0.25))  # Set label locations.
                    axs[each_row, each_col].grid(True,which='minor',linestyle='--',linewidth=0.1)
                    axs[each_row, each_col].grid(True,which='major',linestyle='--',linewidth=0.4)
                    axs[each_row, each_col].tick_params(axis='y',which='major', width=0.5, labelsize=5.5)#X and y labels font size
                    if each_row != (maxrow-1):
                        pyplot.setp(axs[each_row, each_col].get_xmajorticklabels(), visible=False)
                    else:
                        pyplot.setp(axs[each_row, each_col].get_xmajorticklabels(), visible=True)
                
                if each_row == (maxrow-1):
                    axs[each_row, each_col].set_xlabel('Local Time', fontsize = 7)
                    axs[each_row, each_col].set_xticks(numpy.arange(0, 24, step=3))  # Set label locations.
                    axs[each_row, each_col].set_yticks(numpy.arange(0, 1.1, step=0.25))  # Set label locations.
                    axs[each_row, each_col].grid(True,which='minor',linestyle='--',linewidth=0.1)
                    axs[each_row, each_col].grid(True,which='major',linestyle='--',linewidth=0.4)
                    axs[each_row, each_col].tick_params(axis='x',which='major', width=0.7, labelsize=7)#X and y labels font size
                    pyplot.setp(axs[each_row, each_col].get_xmajorticklabels(), visible=True)
                else:
                    axs[each_row, each_col].set_xticks(numpy.arange(0, 24, step=3))  # Set label locations.
                    axs[each_row, each_col].set_yticks(numpy.arange(0, 1.1, step=0.25))  # Set label locations.
                    axs[each_row, each_col].grid(True,which='minor',linestyle='--',linewidth=0.1)
                    axs[each_row, each_col].grid(True,which='major',linestyle='--',linewidth=0.4)
                    pyplot.setp(axs[each_row, each_col].get_xmajorticklabels(), visible=False)

                axs[each_row, each_col].set_ylim(0, 1.1)
                axs[each_row, each_col].set_xlim(0, 24)
                each_col = each_col + 1
                if each_col == maxcol:
                    each_row=each_row+1
                    each_col = 0
                    
#Only to fill blank spaces without satellite data
axs[maxrow-1,  maxcol-1].set_xlabel('Local Time', fontsize = 7)
axs[maxrow-1,  maxcol-1].set_xticks(numpy.arange(0, 24, step=3))  # Set label locations.
axs[maxrow-1,  maxcol-1].set_xticklabels(locallabels)
axs[maxrow-1,  maxcol-1].set_yticks(numpy.arange(0, 1.1, step=0.25))  # Set label locations.
axs[maxrow-1,  maxcol-1].grid(True,which='minor',linestyle='--',linewidth=0.1)
axs[maxrow-1,  maxcol-1].grid(True,which='major',linestyle='--',linewidth=0.4)
axs[maxrow-1,  maxcol-1].tick_params(axis='x',which='major', width=0.7, labelsize=7)#X and y labels font size
pyplot.setp(axs[maxrow-1,  maxcol-1].get_xmajorticklabels(), visible=True)

# Hide x labels and tick labels for top plots and y ticks for right plots.
for ax in axs.flat:
	ax.label_outer()
    
    

pyplot.show()

print("--- %s seconds ---" % (time.time() - start_time))


01_131_S4L1
01_131_S4L2
01_131_ELEV
01_131_TIME
01_131_AZIT
01_131_NSA1
01_131_NSA2
01_133_S4L1
01_133_S4L2
01_133_ELEV
01_133_TIME
01_133_AZIT
01_133_NSA1
01_133_NSA2
01_136_S4L1
01_136_S4L2
01_136_ELEV
01_136_TIME
01_136_AZIT
01_136_NSA1
01_136_NSA2
01_138_S4L1
01_138_S4L2
01_138_ELEV
01_138_TIME
01_138_AZIT
01_138_NSA1
01_138_NSA2
Reading C:\Users\JmGomezs\Documents\Scintpi\data/sc2_lvl2_20210314_0001_768758.0625W_119523.1016S.h5 file
maxsats: 94
GPS 1 0 0 3
GPS 2 1 0 3
GPS 3 2 0 3
GPS 5 3 0 3
GPS 6 4 0 3
GPS 7 0 1 3
GPS 9 1 1 3
GPS10 2 1 3
GPS12 3 1 3
GPS13 4 1 3
GPS14 0 2 3
GPS16 1 2 3
GPS17 2 2 3
GPS18 3 2 3
GPS19 4 2 3
GPS20 0 3 3
GPS21 1 3 3
GPS22 2 3 3
GPS23 3 3 3
GPS24 4 3 3
GPS25 0 4 3
GPS26 1 4 3
GPS27 2 4 3
GPS28 3 4 3
GPS29 4 4 3
GPS30 0 5 3
GPS31 1 5 3
GPS32 2 5 3
Svid: 131
Svid: 133
Svid: 138
GAL 1 1 6 3
GAL 2 2 6 3
GAL 3 3 6 3
GAL 4 4 6 3
GAL 5 0 7 3
GAL 7 1 7 3
GAL 8 2 7 3
GAL 9 3 7 3
GAL11 4 7 3
GAL12 0 8 3
GAL13 1 8 3
GAL15 2 8 3
GAL19 3 8 3
GAL21 4 8 3
GAL25 0 9 3


--- 11.170926570892334 seconds ---
